In [1]:
from dask import delayed
from kmodes.kmodes import KModes
from sklearn.preprocessing import OneHotEncoder
from sklearn.pipeline import make_pipeline

import dask
import numpy as np
import pandas as pd


In [177]:
@delayed
def get_cost(df, k, init):
    km = KModes(n_clusters=k, init=init)
    km.fit_predict(df)
    return km.cost_


def get_fitness(df, k):
    costs = []
    for init in ["cao", "matching_best"]:
        costs.append(get_cost(df, k, init))
    return costs[1] - costs[0]


In [184]:
df = pd.read_csv("../data/zoo.csv")
X = df.drop(["animal_name", "class"], axis=1).values


In [185]:
max_seed = 50
k = 4

costs = np.empty(max_seed, dtype="object")
for seed in range(max_seed):
    np.random.seed(seed)
    costs[seed] = get_fitness(df, k)


In [186]:
dask.visualize(costs.mean(), rankdir="LR")


In [190]:
%%timeit
res = []
for _ in range(100):
    np.random.seed(0)
    pipe = make_pipeline(
        get_fitness(X, 7)
    )
    res.append(pipe)

fitnesses = dask.compute(*[r.steps[0][1] for r in res])

9.9 s ± 145 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [189]:
sorted(fitnesses)


[-5.0,
 -4.0,
 -2.0,
 -1.0,
 0.0,
 0.0,
 2.0,
 3.0,
 3.0,
 4.0,
 4.0,
 4.0,
 5.0,
 5.0,
 5.0,
 5.0,
 5.0,
 5.0,
 6.0,
 6.0,
 7.0,
 7.0,
 7.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 11.0,
 12.0,
 12.0,
 13.0,
 13.0,
 14.0,
 14.0,
 15.0,
 15.0,
 15.0,
 15.0,
 16.0,
 16.0,
 16.0,
 16.0,
 16.0,
 16.0,
 16.0,
 16.0,
 16.0,
 17.0,
 17.0,
 18.0,
 18.0,
 18.0,
 18.0,
 18.0,
 19.0,
 20.0,
 21.0,
 21.0,
 21.0,
 22.0,
 22.0,
 22.0,
 22.0,
 22.0,
 23.0,
 23.0,
 23.0,
 24.0,
 24.0,
 25.0,
 27.0,
 28.0,
 28.0,
 28.0,
 29.0,
 29.0,
 30.0,
 31.0,
 32.0,
 33.0,
 34.0,
 36.0,
 57.0,
 57.0,
 62.0,
 65.0,
 95.0]